<a href="https://colab.research.google.com/github/muasiq/LoveIt/blob/master/Vibration_input_plot_(1).ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install azure-cosmos
!pip install azure-cosmos
!pip install matplotlib
!pip install pandas
!pip install plotly

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 222.8/222.8 KB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 174.5/174.5 KB 19.4 MB/s eta 0:00:00
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


##Libraries and Packages

In [2]:
from statistics import mean
import math
import pytz
import matplotlib.pyplot as plt
import pandas as pd
from azure.cosmos import exceptions, CosmosClient, PartitionKey
from datetime import datetime
from pytz import timezone
import pandas as pd

##Pull Data

In [3]:
endpoint_nosql = 'https://predictive-maintenance-nosql-db.documents.azure.com:443/'
key = 'mf8KHYLgtm5qhYGjohyLiQu5jRP5ynILjM2tzasM9qERKIzWdzHo6myzn5aKGSq6rwpx4E05ADWvACDbA0SnVg=='
client_nosql = CosmosClient(endpoint_nosql, key)

database_name = "IoT-Hub-messages"
try:
    database = client_nosql.create_database(id=database_name)
except exceptions.CosmosResourceExistsError:
    database = client_nosql.get_database_client(database=database_name)

In [4]:
container_name = 'raw_sensor_data'
try:
  container = database.create_container_if_not_exists(
      id=container_name,
      partition_key=PartitionKey(path="/id")
  )
except exceptions.CosmosHttpResponseError:
  container = database.get_container_client(container_name)

In [5]:
from pytz import timezone
startTime =datetime(2023, 2, 1, 0, 0, 0)
endTime =datetime(2023, 2, 28, 11, 30, 0)

start_utc_time = timezone("Asia/Dhaka").localize(startTime)
start_timestamp =datetime.timestamp(start_utc_time)
end_utc_time = timezone("Asia/Dhaka").localize(endTime)
end_timestamp =datetime.timestamp(end_utc_time)

print(start_timestamp)
print(end_timestamp)

1675188000.0
1677562200.0


In [6]:
query = f"SELECT * FROM raw_sensor_data WHERE raw_sensor_data.timestamp BETWEEN {start_timestamp} AND {end_timestamp}"
data = container.query_items(query=query, enable_cross_partition_query=True)

In [7]:
data = list(data)
len(data)

35479

In [8]:
data[0].keys()

dict_keys(['SensorNodeID', 'timestamp', 'Temperature', 'RawSoundValue', 'AccelerometerX', 'AccelerometerY', 'AccelerometerZ', 'GyroscopeX', 'GyroscopeY', 'GyroscopeZ', 'data_entry_timestamp', 'id', '_rid', '_self', '_etag', '_attachments', '_ts'])

In [9]:
cols = ['AccelerometerX', 'AccelerometerY', 'AccelerometerZ', 'GyroscopeX', 'GyroscopeY', 'GyroscopeZ']

##Helping Functions

In [10]:
def find_min(lst : list):
  return min(lst)

In [11]:
def find_pos_lst_mean(lst : list):
  min_value = find_min(lst)
  updated_lst = [x+(-1 * min_value) for x in lst]
  return mean(updated_lst)

In [12]:
def find_rms(lst : list):
  square_lat=[x*x for x in lst]
  return round(math.sqrt(sum(square_lat))/3, 2)

In [13]:
def find_xyz (data : dict):
  out_dict ={}
  out_list = []
  out_dict['AccelerometerX']=find_pos_lst_mean(data['AccelerometerX'])
  out_list.append(find_pos_lst_mean(data['AccelerometerX']))
  out_dict['AccelerometerY']=find_pos_lst_mean(data['AccelerometerY'])
  out_list.append(find_pos_lst_mean(data['AccelerometerY']))
  out_dict['AccelerometerZ']=find_pos_lst_mean(data['AccelerometerZ'])
  out_list.append(find_pos_lst_mean(data['AccelerometerZ']))
  out_dict['GyroscopeX']=find_pos_lst_mean(data['GyroscopeX'])
  out_list.append(find_pos_lst_mean(data['GyroscopeX']))
  out_dict['GyroscopeY']=find_pos_lst_mean(data['GyroscopeY'])
  out_list.append(find_pos_lst_mean(data['GyroscopeY']))
  out_dict['GyroscopeZ']=find_pos_lst_mean(data['GyroscopeZ'])
  out_list.append(find_pos_lst_mean(data['GyroscopeZ']))
  out_dict['Accelerometer_RMS']=find_rms(out_list[0:3])
  out_dict['Gyroscope_RMS']=find_rms(out_list[3:])
  return out_dict
  

In [14]:
find_xyz(data[0])

{'AccelerometerX': 257.0703125,
 'AccelerometerY': 373.3984375,
 'AccelerometerZ': 399.4296875,
 'GyroscopeX': 22.765625,
 'GyroscopeY': 25.9765625,
 'GyroscopeZ': 2.7734375,
 'Accelerometer_RMS': 201.4,
 'Gyroscope_RMS': 11.55}

##Dataframe Vibration Input

In [15]:
df = pd.DataFrame(columns=('datetime','x_accelerometer_value', 'y_accelerometer_value', 'z_accelerometer_value',
                           'x_gyroscope_value', 'y_gyroscope_value','z_gyroscope_value','x_rms', 'y_rms'))
tz = pytz.timezone('Asia/Dhaka')
limit = 0
for idx, data_1 in enumerate(data):
  date_time = str(datetime.fromtimestamp(data[idx]['timestamp'],tz))
  out_dict= find_xyz(data_1 )
  df.loc[idx] = [date_time, out_dict['AccelerometerX'], out_dict['AccelerometerY'], out_dict['AccelerometerZ']
              , out_dict['GyroscopeX'], out_dict['GyroscopeY'], out_dict['GyroscopeZ'],
              out_dict[ 'Accelerometer_RMS'], out_dict['Gyroscope_RMS']]
  limit = limit+1
  '''if limit >1000:
    break'''

In [16]:
df_1= pd.DataFrame(columns=('datetime','x_accelerometer_value', 'y_accelerometer_value', 'z_accelerometer_value',
                           'x_gyroscope_value', 'y_gyroscope_value','z_gyroscope_value','x_rms', 'y_rms'))
tz = pytz.timezone('Asia/Dhaka')
limit = 0
for idx, data_1 in enumerate(data):
  if data_1['SensorNodeID'] == 1:
    date_time = datetime.fromtimestamp(data[idx]['timestamp'],tz)
    out_dict= find_xyz(data_1 )
    df_1.loc[idx] = [date_time, out_dict['AccelerometerX'], out_dict['AccelerometerY'], out_dict['AccelerometerZ']
                , out_dict['GyroscopeX'], out_dict['GyroscopeY'], out_dict['GyroscopeZ'],
                out_dict[ 'Accelerometer_RMS'], out_dict['Gyroscope_RMS']]
    limit = limit+1
    '''if limit >1000:
      break'''

In [17]:
df_2= pd.DataFrame(columns=('datetime','x_accelerometer_value', 'y_accelerometer_value', 'z_accelerometer_value',
                           'x_gyroscope_value', 'y_gyroscope_value','z_gyroscope_value','x_rms', 'y_rms'))
tz = pytz.timezone('Asia/Dhaka')
limit = 0
for idx, data_1 in enumerate(data):
  if data_1['SensorNodeID'] == 2:
    date_time = str(datetime.fromtimestamp(data[idx]['timestamp'],tz))
    out_dict= find_xyz(data_1 )
    df_2.loc[idx] = [date_time, out_dict['AccelerometerX'], out_dict['AccelerometerY'], out_dict['AccelerometerZ']
                , out_dict['GyroscopeX'], out_dict['GyroscopeY'], out_dict['GyroscopeZ'],
                out_dict[ 'Accelerometer_RMS'], out_dict['Gyroscope_RMS']]
    limit = limit+1
    '''if limit >1000:
      break'''

In [18]:
df_3= pd.DataFrame(columns=('datetime','x_accelerometer_value', 'y_accelerometer_value', 'z_accelerometer_value',
                           'x_gyroscope_value', 'y_gyroscope_value','z_gyroscope_value','x_rms', 'y_rms'))
tz = pytz.timezone('Asia/Dhaka')
limit = 0
for idx, data_1 in enumerate(data):
  if data_1['SensorNodeID'] == 3:
    date_time = str(datetime.fromtimestamp(data[idx]['timestamp'],tz))
    out_dict= find_xyz(data_1 )
    df_3.loc[idx] = [date_time, out_dict['AccelerometerX'], out_dict['AccelerometerY'], out_dict['AccelerometerZ']
                , out_dict['GyroscopeX'], out_dict['GyroscopeY'], out_dict['GyroscopeZ'],
                out_dict[ 'Accelerometer_RMS'], out_dict['Gyroscope_RMS']]
    limit = limit+1
    '''if limit >1000:
      break'''

In [19]:
df_4= pd.DataFrame(columns=('datetime','x_accelerometer_value', 'y_accelerometer_value', 'z_accelerometer_value',
                           'x_gyroscope_value', 'y_gyroscope_value','z_gyroscope_value','x_rms', 'y_rms'))
tz = pytz.timezone('Asia/Dhaka')
limit = 0
for idx, data_1 in enumerate(data):
  if data_1['SensorNodeID'] == 4:
    date_time = str(datetime.fromtimestamp(data[idx]['timestamp'],tz))
    out_dict= find_xyz(data_1 )
    df_4.loc[idx] = [date_time, out_dict['AccelerometerX'], out_dict['AccelerometerY'], out_dict['AccelerometerZ']
                , out_dict['GyroscopeX'], out_dict['GyroscopeY'], out_dict['GyroscopeZ'],
                out_dict[ 'Accelerometer_RMS'], out_dict['Gyroscope_RMS']]
    limit = limit+1
    '''if limit >1000:
      break'''

In [20]:
df_5= pd.DataFrame(columns=('datetime','x_accelerometer_value', 'y_accelerometer_value', 'z_accelerometer_value',
                           'x_gyroscope_value', 'y_gyroscope_value','z_gyroscope_value','x_rms', 'y_rms'))
tz = pytz.timezone('Asia/Dhaka')
limit = 0
for idx, data_1 in enumerate(data):
  if data_1['SensorNodeID'] == 5:
    date_time = str(datetime.fromtimestamp(data[idx]['timestamp'],tz))
    out_dict= find_xyz(data_1 )
    df_5.loc[idx] = [date_time, out_dict['AccelerometerX'], out_dict['AccelerometerY'], out_dict['AccelerometerZ']
                , out_dict['GyroscopeX'], out_dict['GyroscopeY'], out_dict['GyroscopeZ'],
                out_dict[ 'Accelerometer_RMS'], out_dict['Gyroscope_RMS']]
    limit = limit+1
    '''if limit >1000:
      break'''

In [21]:
limit

6514

In [22]:
df_1.head()

datetime  x_accelerometer_value  y_accelerometer_value  \
0  2023-02-01 00:03:14+06:00             257.070312             373.398438   
5  2023-02-01 00:08:14+06:00             266.921875             465.242188   
10 2023-02-01 00:13:14+06:00             248.203125             511.734375   
15 2023-02-01 00:18:14+06:00             335.562500             404.351562   
20 2023-02-01 00:23:14+06:00             252.609375             357.179688   

    z_accelerometer_value  x_gyroscope_value  y_gyroscope_value  \
0              399.429688          22.765625          25.976562   
5              359.101562          22.914062          22.320312   
10             388.226562          27.437500          28.281250   
15             391.015625          23.828125          32.093750   
20             488.125000          28.812500          37.500000   

    z_gyroscope_value   x_rms  y_rms  
0            2.773438  201.40  11.55  
5            4.890625  215.16  10.79  
10           4.000000  229.54  13.20  
15           4.007812  218.33  13.39  
20           3.906250  218.49  15.82

In [23]:
df.to_csv('data.csv')

##Visualization

In [24]:
import plotly.express as px
fig_1 = px.scatter(df_1, x='datetime', y='x_rms', height=400)
fig_1.show()

In [25]:
fig_2 = px.scatter(df_2, x='datetime', y='x_rms', height=400)
fig_2.show()

In [26]:
fig_3 = px.line(df_3, x='datetime', y='x_rms', height=400)
fig_3.show()

In [27]:
fig_4 = px.scatter(df_4, x='datetime', y='x_rms', height=400)
fig_4.show()

In [28]:
fig_5 = px.scatter(df_4, x='datetime', y='x_rms', height=400)
fig_5.show()

##Find Trends

In [29]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


##NRR.

In [39]:
path = r'/content/drive/MyDrive/Predictive Maintenance/Datasets/Maintenance df/df_initial_NRR (2).csv'
df_initial_NRR = pd.read_csv(path)

In [40]:
df_initial_NRR['Start time']=df_initial_NRR['Start time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))

In [41]:
df_initial_NRR['Stop time']=df_initial_NRR['Stop time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))

In [42]:
y_1 = pd.DataFrame(columns=list(df_1.columns))

In [43]:
for idx, row in df_initial_NRR.iterrows():
  y_1 = pd.concat([y_1, df_1[(df_1['datetime'] > row['Start time']) & (df_1['datetime'] < row['Stop time'])]], ignore_index=True)
  
  

In [44]:
fig_1 = px.scatter(df_1, x='datetime', y='x_rms', height=400, opacity = 0.2)
fig_1.add_scatter(x=y_1['datetime'], y=y_1['x_rms'], mode='markers')
fig_1.show()

##CHange Over.

In [45]:
#del(y_2)

In [46]:
path = r'/content/drive/MyDrive/Predictive Maintenance/Datasets/Maintenance df/df_initial_change_over.csv'
df_initial_change_over = pd.read_csv(path)
df_initial_change_over['Start time']=df_initial_change_over['Start time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
df_initial_change_over['Stop time']=df_initial_change_over['Stop time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
y_2 = pd.DataFrame(columns=list(df_1.columns))
for idx, row in df_initial_change_over.iterrows():
  y_2 = pd.concat([y_2, df_1[(df_1['datetime'] > row['Start time']) & (df_1['datetime'] < row['Stop time'])]], ignore_index=True)
  

In [47]:
fig_2 = px.scatter(df_1, x='datetime', y='x_rms', height=400, opacity = 0.2)
fig_2.add_scatter(x=y_2['datetime'], y=y_2['x_rms'], mode='markers')
fig_2.show()

Maintenance

In [48]:
path = r'/content/drive/MyDrive/Predictive Maintenance/Datasets/Maintenance df/df_initial_Maintenance.csv'
df_initial_Maintenance = pd.read_csv(path)
df_initial_Maintenance['Start time']=df_initial_Maintenance['Start time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
df_initial_Maintenance['Stop time']=df_initial_Maintenance['Stop time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
y_3 = pd.DataFrame(columns=list(df_1.columns))
for idx, row in df_initial_Maintenance.iterrows():
  y_3 = pd.concat([y_3, df_1[(df_1['datetime'] > row['Start time']) & (df_1['datetime'] < row['Stop time'])]], ignore_index=True)

In [49]:
fig_3 = px.scatter(df_1, x='datetime', y='x_rms', height=400, opacity = 0.2)
fig_3.add_scatter(x=y_3['datetime'], y=y_3['x_rms'], mode='markers')
fig_3.show()

CRS Not Ready.

In [50]:
path = r'/content/drive/MyDrive/Predictive Maintenance/Datasets/Maintenance df/df_initial_CRS.csv'
df_initial_CRS = pd.read_csv(path)
df_initial_CRS['Start time']=df_initial_CRS['Start time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
df_initial_CRS['Stop time']=df_initial_CRS['Stop time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
y_4 = pd.DataFrame(columns=list(df_1.columns))
for idx, row in df_initial_CRS.iterrows():
  y_4 = pd.concat([y_4, df_1[(df_1['datetime'] > row['Start time']) & (df_1['datetime'] < row['Stop time'])]], ignore_index=True)

In [51]:
fig_4 = px.scatter(df_1, x='datetime', y='x_rms', height=400, opacity = 0.2)
fig_4.add_scatter(x=y_4['datetime'], y=y_4['x_rms'], mode='markers')
fig_4.show()

Main Power Off (External).

In [52]:
path = r'/content/drive/MyDrive/Predictive Maintenance/Datasets/Maintenance df/df_initial_Main_Poff.csv'
df_initial_Main_Poff = pd.read_csv(path)
df_initial_Main_Poff['Start time']=df_initial_Main_Poff['Start time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
df_initial_Main_Poff['Stop time']=df_initial_Main_Poff['Stop time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
y_5 = pd.DataFrame(columns=list(df_1.columns))
for idx, row in df_initial_Main_Poff.iterrows():
  y_5 = pd.concat([y_5, df_1[(df_1['datetime'] > row['Start time']) & (df_1['datetime'] < row['Stop time'])]], ignore_index=True)

In [53]:
fig_5 = px.scatter(df_1, x='datetime', y='x_rms', height=400, opacity = 0.2)
fig_5.add_scatter(x=y_5['datetime'], y=y_5['x_rms'], mode='markers')
fig_5.show()

Lamina not ready due to Bulking. (Bin # 3 Block Empty for Maitenance)

In [54]:
path = r'/content/drive/MyDrive/Predictive Maintenance/Datasets/Maintenance df/df_initial_Bin3_block_empty.csv'
df_initial_Bin3_block_empty = pd.read_csv(path)
df_initial_Bin3_block_empty['Start time']=df_initial_Bin3_block_empty['Start time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
df_initial_Bin3_block_empty['Stop time']=df_initial_Bin3_block_empty['Stop time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
y_6 = pd.DataFrame(columns=list(df_1.columns))
for idx, row in df_initial_Bin3_block_empty.iterrows():
  y_6 = pd.concat([y_6, df_1[(df_1['datetime'] > row['Start time']) & (df_1['datetime'] < row['Stop time'])]], ignore_index=True)

In [55]:
fig_6 = px.scatter(df_1, x='datetime', y='x_rms', height=400, opacity = 0.2)
fig_6.add_scatter(x=y_6['datetime'], y=y_6['x_rms'], mode='markers')
fig_6.show()

Lamina not ready due to Bulking. (Bin # 3 Traverse Trolley fault )

In [56]:
path = r'/content/drive/MyDrive/Predictive Maintenance/Datasets/Maintenance df/df_initial_Bin3_traverse_trolley.csv'
df_initial_Bin3_traverse_trolley = pd.read_csv(path)
df_initial_Bin3_traverse_trolley['Start time']=df_initial_Bin3_traverse_trolley['Start time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
df_initial_Bin3_traverse_trolley['Stop time']=df_initial_Bin3_traverse_trolley['Stop time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
y_7 = pd.DataFrame(columns=list(df_1.columns))
for idx, row in df_initial_Bin3_traverse_trolley.iterrows():
  y_7 = pd.concat([y_7, df_1[(df_1['datetime'] > row['Start time']) & (df_1['datetime'] < row['Stop time'])]], ignore_index=True)

In [57]:
fig_7 = px.scatter(df_1, x='datetime', y='x_rms', height=400, opacity = 0.2)
fig_7.add_scatter(x=y_7['datetime'], y=y_7['x_rms'], mode='markers')
fig_7.show()

Lamina Sieve Conv. Chute Jam.

In [58]:
path = r'/content/drive/MyDrive/Predictive Maintenance/Datasets/Maintenance df/df_initial_lamina_Sieve_Conv.csv'
df_initial_lamina_Sieve_Conv = pd.read_csv(path)
df_initial_lamina_Sieve_Conv['Start time']=df_initial_lamina_Sieve_Conv['Start time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
df_initial_lamina_Sieve_Conv['Stop time']=df_initial_lamina_Sieve_Conv['Stop time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
y_8 = pd.DataFrame(columns=list(df_1.columns))
for idx, row in df_initial_lamina_Sieve_Conv.iterrows():
  y_8 = pd.concat([y_8, df_1[(df_1['datetime'] > row['Start time']) & (df_1['datetime'] < row['Stop time'])]], ignore_index=True)

In [59]:
fig_8 = px.scatter(df_1, x='datetime', y='x_rms', height=400, opacity = 0.2)
fig_8.add_scatter(x=y_8['datetime'], y=y_8['x_rms'], mode='markers')
fig_8.show()

I0019 m2 Drive Belt Motor Fault.

In [60]:
path = r'/content/drive/MyDrive/Predictive Maintenance/Datasets/Maintenance df/df_initial_drive_belt_motor.csv'
df_initial_drive_belt_motor = pd.read_csv(path)
df_initial_drive_belt_motor['Start time']=df_initial_drive_belt_motor['Start time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
df_initial_drive_belt_motor['Stop time']=df_initial_drive_belt_motor['Stop time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
y_9 = pd.DataFrame(columns=list(df_1.columns))
for idx, row in df_initial_drive_belt_motor.iterrows():
  y_9 = pd.concat([y_9, df_1[(df_1['datetime'] > row['Start time']) & (df_1['datetime'] < row['Stop time'])]], ignore_index=True)

In [61]:
fig_9 = px.scatter(df_1, x='datetime', y='x_rms', height=400, opacity = 0.2)
fig_9.add_scatter(x=y_9['datetime'], y=y_9['x_rms'], mode='markers')
fig_9.show()

Lamina not ready due to bulking.', '

In [62]:
path = r'/content/drive/MyDrive/Predictive Maintenance/Datasets/Maintenance df/df_initial_bulking.csv'
df_initial_bulking = pd.read_csv(path)
df_initial_bulking['Start time']=df_initial_bulking['Start time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
df_initial_bulking['Stop time']=df_initial_bulking['Stop time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
y_10 = pd.DataFrame(columns=list(df_1.columns))
for idx, row in df_initial_bulking.iterrows():
  y_10 = pd.concat([y_10, df_1[(df_1['datetime'] > row['Start time']) & (df_1['datetime'] < row['Stop time'])]], ignore_index=True)

In [63]:
fig_10 = px.scatter(df_1, x='datetime', y='x_rms', height=400, opacity = 0.2)
fig_10.add_scatter(x=y_10['datetime'], y=y_10['x_rms'], mode='markers')
fig_10.show()

Power fail . (Extranal)

In [64]:
path = r'/content/drive/MyDrive/Predictive Maintenance/Datasets/Maintenance df/df_initial_powerfail.csv'
df_initial_powerfail = pd.read_csv(path)
df_initial_powerfail['Start time']=df_initial_powerfail['Start time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
df_initial_powerfail['Stop time']=df_initial_powerfail['Stop time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
y_11 = pd.DataFrame(columns=list(df_1.columns))
for idx, row in df_initial_powerfail.iterrows():
  y_11 = pd.concat([y_11, df_1[(df_1['datetime'] > row['Start time']) & (df_1['datetime'] < row['Stop time'])]], ignore_index=True)

In [65]:
fig_11 = px.scatter(df_1, x='datetime', y='x_rms', height=400, opacity = 0.2)
fig_11.add_scatter(x=y_11['datetime'], y=y_11['x_rms'], mode='markers')
fig_11.show()

FPB#02 travel time out alarm.

In [66]:
path = r'/content/drive/MyDrive/Predictive Maintenance/Datasets/Maintenance df/df_initial_travel_time_out_alarm.csv'
df_initial_travel_time_out_alarm= pd.read_csv(path)
df_initial_travel_time_out_alarm['Start time']=df_initial_travel_time_out_alarm['Start time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
df_initial_travel_time_out_alarm['Stop time']=df_initial_travel_time_out_alarm['Stop time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
y_12 = pd.DataFrame(columns=list(df_1.columns))
for idx, row in df_initial_travel_time_out_alarm.iterrows():
  y_12 = pd.concat([y_12, df_1[(df_1['datetime'] > row['Start time']) & (df_1['datetime'] < row['Stop time'])]], ignore_index=True)

In [67]:
fig_12 = px.scatter(df_1, x='datetime', y='x_rms', height=400, opacity = 0.2)
fig_12.add_scatter(x=y_12['datetime'], y=y_12['x_rms'], mode='markers')
fig_12.show()

FPB delivery con. Jam.

In [68]:
path = r'/content/drive/MyDrive/Predictive Maintenance/Datasets/Maintenance df/df_initial_FPB_delivery.csv'
df_initial_FPB_delivery = pd.read_csv(path)
df_initial_FPB_delivery['Start time']=df_initial_FPB_delivery['Start time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
df_initial_FPB_delivery['Stop time']=df_initial_FPB_delivery['Stop time'].apply(lambda r : pytz.timezone('Asia/Dhaka').localize(datetime.strptime(r, '%Y-%m-%d %H:%M:%S')))
y_13 = pd.DataFrame(columns=list(df_1.columns))
for idx, row in df_initial_FPB_delivery.iterrows():
  y_13 = pd.concat([y_13, df_1[(df_1['datetime'] > row['Start time']) & (df_1['datetime'] < row['Stop time'])]], ignore_index=True)

In [69]:
fig_13 = px.scatter(df_1, x='datetime', y='x_rms', height=400, opacity = 0.2)
fig_13.add_scatter(x=y_13['datetime'], y=y_13['x_rms'], mode='markers')
fig_13.show()